In [1]:
import os
import folium
import pandas as pd
import numpy as np
import networkx as nx
from haversine import haversine
from geopy.geocoders import Nominatim
from geopy.extra.rate_limiter import RateLimiter
import googlemaps

In [3]:
car = pd.read_csv('data/Jeju_car.csv', encoding='cp949')
car

시도     소방서           센터    지역대    분류명  수량   latitude   longitude
0   제주특별자치도  소방안전본부        소방정책과    NaN    승합형   2  33.490524  126.498981
1   제주특별자치도   제주소방서      이도119센터    NaN  음압구급차   1  33.491107  126.536502
2   제주특별자치도   제주소방서      이도119센터    NaN    승합형   1  33.491107  126.536502
3   제주특별자치도   제주소방서      삼도119센터    NaN    승합형   1  33.515851  126.517085
4   제주특별자치도   제주소방서      오라119센터    NaN    승합형   1  33.497296  126.514680
5   제주특별자치도   제주소방서      연동119센터    NaN    승합형   1  33.488427  126.497116
6   제주특별자치도   제주소방서      항만119센터    NaN    승합형   2  33.519988  126.539069
7   제주특별자치도   제주소방서      화북119센터    NaN    승합형   1  33.519376  126.573533
8   제주특별자치도   동부소방서      구좌119센터    NaN    승합형   1  33.520067  126.860112
9   제주특별자치도   동부소방서      조천119센터    NaN    승합형   1  33.541011  126.646849
10  제주특별자치도   제주소방서      노형119센터    NaN    승합형   1  33.481020  126.472278
11  제주특별자치도   제주소방서      외도119센터    NaN    승합형   1  33.486565  126.437509
12  제주특별자치도   제주소방서      아라119센터    NaN    승합형   1  33.467963  126.565735
13  제주특별자치도   동부소방서      구좌119센터  김녕지역대    승합형   1  33.554153  126.762754
14  제주특별자치도  서귀포소방서      동홍119센터    NaN    승합형   1  33.554153  126.762754
15  제주특별자치도  서귀포소방서      중문119센터    NaN    승합형   1  33.254116  126.438091
16  제주특별자치도   동부소방서      성산119센터    NaN  음압구급차   1  33.460263  126.909673
17  제주특별자치도   동부소방서      성산119센터    NaN    승합형   1  33.460263  126.909673
18  제주특별자치도   동부소방서      표선119센터    NaN    승합형   1  33.327079  126.827741
19  제주특별자치도   동부소방서      남원119센터    NaN    승합형   2  33.281482  126.708404
20  제주특별자치도  서귀포소방서      효돈119센터    NaN    승합형   1  33.260720  126.607779
21  제주특별자치도  서귀포소방서      대신119센터    NaN    승합형   2  33.249538  126.514155
22  제주특별자치도   동부소방서      표선119센터  성읍지역대    승합형   1  33.383164  126.794483
23  제주특별자치도  서귀포소방서        현장대응과    NaN    승합형   2  33.249493  126.514166
24  제주특별자치도   서부소방서      한림119센터    NaN    승합형   2  33.402464  126.270362
25  제주특별자치도   서부소방서      애월119센터    NaN    승합형   1  33.466598  126.348748
26  제주특별자치도   서부소방서      한경119센터    NaN    승합형   1  33.342619  126.182869
27  제주특별자치도   서부소방서      대정119센터    NaN    승합형   1  33.232472  126.240922
28  제주특별자치도   서부소방서      안덕119센터    NaN    승합형   1  33.251144  126.330807
29  제주특별자치도   서부소방서  영어교육도시119센터    NaN    승합형   1  33.278920  126.273334
30  제주특별자치도   서부소방서        현장대응과    NaN    승합형   1  33.402363  126.270390

In [4]:
nodes = pd.read_csv('data/Jeju_nodes.csv', encoding='utf-8')
links = pd.read_csv('data/Jeju_links.csv', encoding='cp949')

nodes = nodes[['Id','NODE_NAME','latitude','longitude']]
links = links[['Source','Target']]
source_in = links['Source'].apply(lambda x : x in list(nodes['Id'])) # check Sources are in jeju
target_in = links['Target'].apply(lambda x : x in list(nodes['Id'])) # check Targets are in jeju
# source_in and target_in are boolean type pandas.Series which contains True or False
jeju_links = links[source_in & target_in] # contain if both target and source are contained in jeju

In [6]:
G = nx.Graph()
# R is the Earth's radius
R = 6371e3

for idx,row in nodes.iterrows():
    # add node to Graph G
    G.add_node(row['Id'],Label=row['NODE_NAME'],latitude=row['latitude'], longitude=row['longitude'])

for idx,row in jeju_links.iterrows():
    ## Calculate the distance between Source and Target Nodes
    lon1 = float(nodes[nodes['Id'] == row['Source']]['longitude'] * np.pi/180)
    lat1 = float(nodes[nodes['Id'] == row['Source']]['latitude'] * np.pi/180)
    lon2 = float(nodes[nodes['Id'] == row['Target']]['longitude'] * np.pi/180)
    lat2 = float(nodes[nodes['Id'] == row['Target']]['latitude'] * np.pi/180)
    d_lat = lat2 - lat1
    d_lon = lon2 - lon1
    a = np.sin(d_lat/2) ** 2 + np.cos(lat1) * np.cos(lat2) * np.sin(d_lon/2) ** 2
    c = 2 * np.arctan2(a**0.5, (1-a) ** 0.5)
    d = R * c
    
    # Link attribute : 'Source', 'Target' and weight = 'Length between them'
    G.add_edge(row['Source'],row['Target'],weight = d)

C:\Flutter\bin\ipykernel_21588\2128013144.py:11: FutureWarning: Calling float on a single element Series is deprecated and will raise a TypeError in the future. Use float(ser.iloc[0]) instead
  lon1 = float(nodes[nodes['Id'] == row['Source']]['longitude'] * np.pi/180)
C:\Flutter\bin\ipykernel_21588\2128013144.py:12: FutureWarning: Calling float on a single element Series is deprecated and will raise a TypeError in the future. Use float(ser.iloc[0]) instead
  lat1 = float(nodes[nodes['Id'] == row['Source']]['latitude'] * np.pi/180)
C:\Flutter\bin\ipykernel_21588\2128013144.py:13: FutureWarning: Calling float on a single element Series is deprecated and will raise a TypeError in the future. Use float(ser.iloc[0]) instead
  lon2 = float(nodes[nodes['Id'] == row['Target']]['longitude'] * np.pi/180)
C:\Flutter\bin\ipykernel_21588\2128013144.py:14: FutureWarning: Calling float on a single element Series is deprecated and will raise a TypeError in the future. Use float(ser.iloc[0]) instead
  

In [7]:
def connectRes(graph, df): # df는 idx, latitude, longitude가 있어야함
    nodes_latitude = nx.get_node_attributes(graph, 'latitude')
    nodes_longitude = nx.get_node_attributes(graph, 'longitude')
    for idx, row in df.iterrows():
        distances ={}
        for keyLong, valLat in nodes_latitude.items():
            nodesPos = (valLat, nodes_longitude[keyLong])
            curPos = (row['latitude'], row['longitude'])
            distances[keyLong] = haversine(nodesPos, curPos, unit='km')
        nearest_node = min(distances, key=distances.get)
        graph.add_node(idx, Label=idx, latitude=row['latitude'], longitude=row['longitude']) ##노드이름은 4050000000이하로 설정
        graph.add_edge(nearest_node, idx, weight=distances[nearest_node]) 
    return graph

G = connectRes(G, car)
print(f"Data: {len(car)}, Nodes: {len(G.nodes)}, Edges: {len(G.edges)}")

Data: 31, Nodes: 4249, Edges: 6046


In [8]:
# Positioning the Standard Point for our Folium Map
std_point = tuple(nodes.head(1)[['latitude','longitude']].iloc[0])
std_point

(33.25467814707047, 126.5127347346484)

In [9]:
map_osm = folium.Map(location=std_point, zoom_start=10) 

kw = {'opacity': 0.5, 'weight': 2}
for ix, row in jeju_links.iterrows():
    start = tuple(nodes[nodes['Id']==row['Source']][['latitude','longitude']].iloc[0])
    end = tuple(nodes[nodes['Id']==row['Target']][['latitude','longitude']].iloc[0])
    folium.PolyLine(
        locations=[start, end],
        color='blue',
        line_cap='round',
        **kw,
    ).add_to(map_osm)
# it takes some time.....

for ix, row in car.iterrows():
    location = (row['latitude'], row['longitude']) # 위도, 경도 튜플
    folium.Circle(
        location=location,
        radius=500, 
        color='white',
        weight=1,
        fill_opacity=0.6,
        opacity=1,
        fill_color='red',
        fill=True,  # gets overridden by fill_color
        # popup=str(row['Id'])
    ).add_to(map_osm)
    # folium.Marker(location, popup=row['NODE_NAME']).add_to(map_osm)

map_osm